The dataset must first be 'cleaned up' to only include elements of interest. But first import the necessary packages:

In [25]:
import pandas as pd
import geopandas as gpd
import folium
import ipyleaflet

Open data. Note file is not in UTF-8 encoding, therefore clean up prior to opening.

In [4]:
# Load with cp1252 (or ISO-8859-1) to avoid Unicode error
repd_data = pd.read_csv('repd-q4-jan-2025.csv', encoding='cp1252')

# Then normalize any weird characters if needed
repd_data = repd_data.map(lambda x: x.replace('\xa0', ' ') if isinstance(x, str) else x)

repd_data.head() # show raw data

Old Ref ID  Ref ID Record Last Updated (dd/mm/yyyy)  \
0    N00053B       1                       07/07/2009   
1      AA110       2                       20/11/2017   
2      B0730       3                       20/12/2019   
3    1106000       4                       18/12/2003   
4                  5                       29/09/2005   

                       Operator (or Applicant)  \
0                                   RWE npower   
1  Orsted (formerly Dong Energy) / Peel Energy   
2           Scottish and Southern Energy (SSE)   
3                       Energy Power Resources   
4                                      Agrigen   

                        Site Name      Technology Type Storage Type  \
0  Aberthaw Power Station Biomass  Biomass (co-firing)          NaN   
1           Hunterston - cofiring  Biomass (co-firing)          NaN   
2   Ferrybridge Multifuel 2 (FM2)     EfW Incineration          NaN   
3  Thetford Biomass Power Station  Biomass (dedicated)          NaN   
4   Nunn Mills Road Biomass Plant  Biomass (dedicated)          NaN   

  Storage Co-location REPD Ref ID Installed Capacity (MWelec)  \
0                             NaN                          35   
1                             NaN                         170   
2                             NaN                          70   
3                             NaN                        38.5   
4                             NaN                         8.8   

  Share Community Scheme  ... Appeal Granted Planning Permission Granted  \
0                    NaN  ...            NaN                  03/09/2004   
1                    NaN  ...            NaN                         NaN   
2                    NaN  ...            NaN                  28/10/2015   
3                    NaN  ...            NaN                  05/05/1995   
4                    NaN  ...            NaN                         NaN   

  Secretary of State - Intervened Secretary of State - Refusal  \
0                             NaN                          NaN   
1                             NaN                          NaN   
2                             NaN                          NaN   
3                             NaN                          NaN   
4                             NaN                          NaN   

  Secretary of State - Granted Planning Permission Expired Under Construction  \
0                          NaN                         NaN         01/05/2006   
1                          NaN                         NaN                NaN   
2                          NaN                  28/10/2020         01/09/2016   
3                          NaN                         NaN                NaN   
4                          NaN                         NaN                NaN   

  Operational Heat Network Ref Solar Site Area (sqm)  
0  01/05/2007              NaN                   NaN  
1         NaN              NaN                   NaN  
2  20/12/2019              NaN                   NaN  
3  02/10/1998              NaN                   NaN  
4         NaN              NaN                   NaN  

[5 rows x 53 columns]


Clean up column headings adding '_' instead of ' '

Filter data to include only wind turbines

Filter out unneccessary data columns (e.g. related to other technologies, reference numbers used only by REPD data etc)


In [15]:
repd_data = repd_data[repd_data['Technology Type'] == 'Wind Onshore']
repd_wind = repd_data.drop(columns=['Old Ref ID', 'Ref ID', 'Technology Type', 'Storage Type', 'CHP Enabled', 'Storage Co-location REPD Ref ID', 'Share Community Scheme', 'CfD Allocation Round', 'RO Banding (ROC/MWh)', 'CfD Capacity (MW)', 'Mounting Type for Solar', 'Are they re-applying (New REPD Ref)', 'Are they re-applying (Old REPD Ref) ', 'Development Status', 'Offshore Wind Round', 'Heat Network Ref', 'Solar Site Area (sqm)' ])
repd_wind.head() #check if successful

Record Last Updated (dd/mm/yyyy)         Operator (or Applicant)  \
2068                       03/08/2005                      Ecotricity   
2069                       02/05/2006  Western Windpower / Ecotricity   
2070                       27/10/2009                      ECONET LTD   
2071                       09/05/2013                      Ecotricity   
2072                       04/12/2008  LRZ Ltd (Taken over by NOVERA)   

                                Site Name Installed Capacity (MWelec)  \
2068                Stockton Wind Turbine                         1.5   
2069                Brundish Wind Turbine                         1.5   
2070            Yare Estuary Wind Turbine                         1.5   
2071  South Beach Wind Turbine (Somerton)                         1.5   
2072       Swaffham 1 - Ecotech Wind Park                         1.5   

     FiT Tariff (p/kWh) Turbine Capacity No. of Turbines  \
2068                NaN              NaN             NaN   
2069                NaN              NaN             NaN   
2070                NaN             0.37               4   
2071                NaN             1.47               1   
2072                NaN             1.47               1   

     Height of Turbines (m) Development Status (short)  \
2068                    NaN        Application Refused   
2069                    NaN        Application Refused   
2070                    NaN                  Abandoned   
2071                    NaN                Operational   
2072                    NaN                Operational   

                                                Address  ... Appeal Withdrawn  \
2068  East of Layden Lane\r\nTrack\r\nNorwich\r\nNor...  ...              NaN   
2069             East of Brundish Road Stockton Norfolk  ...              NaN   
2070          South Denes Road, Great Yarmouth, Norfolk  ...              NaN   
2071                  Somerton, Great Yarmouth, Norfolk  ...              NaN   
2072      East of West Acre Road\r\nSwaffham\r\nNorfolk  ...              NaN   

     Appeal Refused Appeal Granted Planning Permission Granted  \
2068            NaN            NaN                         NaN   
2069            NaN            NaN                         NaN   
2070            NaN            NaN                  28/04/2000   
2071            NaN            NaN                  28/04/2000   
2072            NaN            NaN                  19/02/1999   

     Secretary of State - Intervened Secretary of State - Refusal  \
2068                             NaN                          NaN   
2069                             NaN                          NaN   
2070                             NaN                          NaN   
2071                             NaN                          NaN   
2072                             NaN                          NaN   

     Secretary of State - Granted Planning Permission Expired  \
2068                          NaN                         NaN   
2069                          NaN                         NaN   
2070                          NaN                         NaN   
2071                          NaN                         NaN   
2072                          NaN                         NaN   

     Under Construction Operational  
2068                NaN         NaN  
2069                NaN         NaN  
2070                NaN         NaN  
2071                NaN  22/07/2000  
2072                NaN  16/08/1999  

[5 rows x 36 columns]

Now convert the tabular data into vector format using the 'X-coordinate' and 'Y-coordinate' columns

In [16]:
# Create the GeoDataFrame
wind_turbines = gpd.GeoDataFrame(repd_wind,
    geometry=gpd.points_from_xy(repd_wind['X-coordinate'], repd_wind['Y-coordinate']),  # Create geometry from X, Y coordinate columns
    crs='epsg:27700') # set crs to British National Grid

wind_turbines.head()

Record Last Updated (dd/mm/yyyy)         Operator (or Applicant)  \
2068                       03/08/2005                      Ecotricity   
2069                       02/05/2006  Western Windpower / Ecotricity   
2070                       27/10/2009                      ECONET LTD   
2071                       09/05/2013                      Ecotricity   
2072                       04/12/2008  LRZ Ltd (Taken over by NOVERA)   

                                Site Name Installed Capacity (MWelec)  \
2068                Stockton Wind Turbine                         1.5   
2069                Brundish Wind Turbine                         1.5   
2070            Yare Estuary Wind Turbine                         1.5   
2071  South Beach Wind Turbine (Somerton)                         1.5   
2072       Swaffham 1 - Ecotech Wind Park                         1.5   

     FiT Tariff (p/kWh) Turbine Capacity No. of Turbines  \
2068                NaN              NaN             NaN   
2069                NaN              NaN             NaN   
2070                NaN             0.37               4   
2071                NaN             1.47               1   
2072                NaN             1.47               1   

     Height of Turbines (m) Development Status (short)  \
2068                    NaN        Application Refused   
2069                    NaN        Application Refused   
2070                    NaN                  Abandoned   
2071                    NaN                Operational   
2072                    NaN                Operational   

                                                Address  ... Appeal Refused  \
2068  East of Layden Lane\r\nTrack\r\nNorwich\r\nNor...  ...            NaN   
2069             East of Brundish Road Stockton Norfolk  ...            NaN   
2070          South Denes Road, Great Yarmouth, Norfolk  ...            NaN   
2071                  Somerton, Great Yarmouth, Norfolk  ...            NaN   
2072      East of West Acre Road\r\nSwaffham\r\nNorfolk  ...            NaN   

     Appeal Granted Planning Permission Granted  \
2068            NaN                         NaN   
2069            NaN                         NaN   
2070            NaN                  28/04/2000   
2071            NaN                  28/04/2000   
2072            NaN                  19/02/1999   

     Secretary of State - Intervened Secretary of State - Refusal  \
2068                             NaN                          NaN   
2069                             NaN                          NaN   
2070                             NaN                          NaN   
2071                             NaN                          NaN   
2072                             NaN                          NaN   

     Secretary of State - Granted Planning Permission Expired  \
2068                          NaN                         NaN   
2069                          NaN                         NaN   
2070                          NaN                         NaN   
2071                          NaN                         NaN   
2072                          NaN                         NaN   

     Under Construction Operational               geometry  
2068                NaN         NaN  POINT (639100 293300)  
2069                NaN         NaN  POINT (639700 294700)  
2070                NaN         NaN  POINT (653400 303800)  
2071                NaN  22/07/2000  POINT (646953 318736)  
2072                NaN  16/08/1999  POINT (581585 309935)  

[5 rows x 37 columns]

Open data in Folium Map to see how it looks

In [24]:
wind_turbines.crs

<Projected CRS: EPSG:27700>
Name: OSGB36 / British National Grid
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: United Kingdom (UK) - offshore to boundary of UKCS within 49°45'N to 61°N and 9°W to 2°E; onshore Great Britain (England, Wales and Scotland). Isle of Man onshore.
- bounds: (-9.01, 49.75, 2.01, 61.01)
Coordinate Operation:
- name: British National Grid
- method: Transverse Mercator
Datum: Ordnance Survey of Great Britain 1936
- Ellipsoid: Airy 1830
- Prime Meridian: Greenwich

In [26]:
m = wind_turbines.explore('Development Status (short)', cmap='viridis', tiles='OpenStreetMap' ) # use development status to display the initial information on the map
# add the wind turbine points to the existing map
#wind_turbines.explore('Site Name',
                # m=m, # add the markers to the same map we just created
                # marker_type='marker', # use a marker for the points, instead of a circle
                # popup=True, # show the information as a popup when we click on the marker
                # legend=False, # don't show a separate legend for the point layer
               # )
m # show the map